In [1]:
import pandas as pd
import torch
from torch.nn import functional as F
from torch.utils.data import DataLoader, Dataset
from transformers import AutoTokenizer, ElectraForSequenceClassification, AdamW
from tqdm.notebook import tqdm
import gc
from sklearn.model_selection import KFold
import numpy as np
import os

In [189]:
torch.__version__

'1.7.1'

In [191]:
device = torch.device("cuda:0")
MODEL_NAME = "monologg/koelectra-small-v3-discriminator"
pre_MODEL_NAME = "result/MODEL_KoELECTRA-Small-v3-discriminator__3.pt"
DATA_PATH = "data/test/"
OUTPUT_PATH = "data/results/"
models = [['Final_FastText', 17], ['Final_FastText', 8]]

In [192]:
#naver movie, Hotel, shopping 
class NHSDataset(Dataset): 
  
    def __init__(self, csv_file):
        self.dataset = csv_file
        self.tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)
  
    def __len__(self):
        return len(self.dataset)
  
    def __getitem__(self, idx):
        row = self.dataset.iloc[idx]
        rawSentenceIdx = row[0]
        text = row[2]
        inputs = self.tokenizer(
            text, 
            return_tensors='pt',
            truncation=True,
            max_length=256,
            pad_to_max_length=True,
            add_special_tokens=True
            )
        input_ids = inputs['input_ids'][0]
        attention_mask = inputs['attention_mask'][0]

        return input_ids, attention_mask, text, rawSentenceIdx

In [193]:


def init(dataFileName, k):
    test_dataset = data_load(dataFileName, k)
    category = category_name_load(dataFileName, k)
    model = model_setting()
    gc.collect()
    torch.cuda.empty_cache()
    
    results = model_predict(model, test_dataset, category)
    
    output_save(results, dataFileName, k)

def output_save(results, dataFileName, k):
    df = pd.DataFrame(results)
    outFileName = OUTPUT_PATH + dataFileName + '_' + str(k) + '_sentiment_results.txt'
    df.columns = ['text', 'category', 'sentiment', 'rawsentenceIdx']
    df.to_csv(outFileName, index = False)
    
def data_load(dataFileName, k):
    categoryResultFile = DATA_PATH + dataFileName + '_' + str(k) + '_results.txt'
    category = pd.read_csv(categoryResultFile, sep= ',')
    categoryCnt = len(category['1'].unique())
        
    test_dataset = []
    for i in range(categoryCnt):
        tmp = category.groupby('1').get_group(i)
        test_dataset.append(NHSDataset(tmp)) 
    return test_dataset

def category_name_load(dataFileName, k):
    wordoutfile = DATA_PATH + dataFileName + '_' + str(k) + '_category.txt'
    category = pd.read_csv(wordoutfile, sep= ',')
    category = category['0']
    category = category.tolist()
    return category   

def model_setting():
    model = ElectraForSequenceClassification.from_pretrained(MODEL_NAME).to(device)
    model.load_state_dict(torch.load(pre_MODEL_NAME))
    return model

def model_predict(model, test_dataset, category):
    model.eval()
    batch_size = 8
    full_result = []
    for cluster_idx, test_data in enumerate(test_dataset):
        test_loader = DataLoader(test_data, batch_size=batch_size)
        
        for input_ids_batch, attention_masks_batch, original_text, rawSentenceIdx in tqdm(test_loader):
            y_pred = model(input_ids_batch.to(device), attention_mask=attention_masks_batch.to(device))[0]
            for idx in range(len(y_pred)):
                pred_tensor = F.sigmoid(y_pred[idx])
                flag = np.argmax([pred_tensor[0], pred_tensor[1]])
                
                tmp = [original_text[idx],category[cluster_idx], flag, rawSentenceIdx[idx].item()]
                full_result.append(tmp)
    return full_result

for model in models:
    init(model[0], model[1])

Some weights of the model checkpoint at monologg/koelectra-small-v3-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.weight', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at monologg/koelectra-small-v3-discriminator and are newly initialized

  0%|          | 0/76 [00:00<?, ?it/s]

  0%|          | 0/137 [00:00<?, ?it/s]

  0%|          | 0/58 [00:00<?, ?it/s]

  0%|          | 0/12 [00:00<?, ?it/s]

...

  0%|          | 0/79 [00:00<?, ?it/s]

  0%|          | 0/128 [00:00<?, ?it/s]

  0%|          | 0/106 [00:00<?, ?it/s]

  0%|          | 0/33 [00:00<?, ?it/s]

  0%|          | 0/40 [00:00<?, ?it/s]

In [156]:
init('1')

Some weights of the model checkpoint at monologg/koelectra-small-v3-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.weight', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at monologg/koelectra-small-v3-discriminator and are newly initialized

  0%|          | 0/9 [00:00<?, ?it/s]

E:\Build\Project\programmers\4_party_project\env\lib\site-packages\transformers\tokenization_utils_base.py:2149: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(
E:\Build\Project\programmers\4_party_project\env\lib\site-packages\torch\nn\functional.py:1639: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")


['도보로도 충분히 갈 수 있는 편리한 거리에 호텔 바로 앞 장충체육관 근처로 요거프레소와 편의점도 있어 편리했습니다', '주변', 1, 6]
['2 식당 한 중 일 식당으로 유명하죠', '주변', 0, 6]
['그냥 가보세요', '주변', 0, 68]
['영빈관 뷰도 좋아요', '주변', 1, 90]
['연결도 없고 그냥 짐 들고 올라가야 하니까요', '주변', 0, 97]
['하지만 주변에 이용할 만한 것들이 부족해서 다소 편의성은 떨어집니다', '주변', 0, 124]
['레스토랑 부대시설 다 좋음', '주변', 1, 153]
['워낙 유명하니', '주변', 0, 163]
['매끼니 걱정할 필요 없고', '주변', 1, 249]
['편의 등 등', '주변', 1, 380]
['다만 주차장과 연결 되어 있지 않아 아쉬웠습니다', '주변', 1, 403]
['영빈관 뷰 아름답고 좋습니다', '주변', 1, 430]
['주변에 즐길거리가 없어서 호텔 내 시설을 최대한 이용하는 것이 좋을 것 같습니다', '주변', 0, 498]
['산책할 수 있는 공간 편안히 즐겼던', '주변', 1, 661]
['이게 호텔이지 느끼게 해줌 편의점이 멈ㅠ 서민 마인드', '주변', 0, 674]
['남산이 한 눈에 들어오는 뷰라서 좋았고 호텔 주위를 볼 수 있어 좋았습니다', '주변', 1, 705]
['최근에 다른 호텔에 가면 지하에 씨유 편의점이 있더라고요 룸에 있는 미니바 이용이 맞긴 한데', '주변', 0, 812]
['개인적 욕심으로 여기도 지하 쇼핑 아케이드에 편 의점 매장 하나 있으면 좋겠다 싶었습니다', '주변', 0, 812]
['그리고 1층 식당 너무 비싼데 맛이 없어요 ㅠㅠ', '주변', 0, 896]
['저녁에는 일몰도 이 쁘게 볼 수 있었습 니다 가까운 거리에 이태원 디 뮤지엄이 있어 문화생활을 하기에도 좋은 위치라고 생각이 들었습니다', '주변', 1, 965]
['4시간 저온 가열했다고 합니다', '주변', 0, 970]
['괜히 유명한 게 아닌 것 

  0%|          | 0/146 [00:00<?, ?it/s]

...

['클럽룸으로 이그제큐티브 라운지를 이용하였는데 총 네 번 이용했어요', '수영장', 1, 1]
['호캉스를 한다면 클럽 룸을 추천해요', '수영장', 1, 1]
['실내 수영장도 개방형이라서 좋았다', '수영장', 1, 3]
['수영장 샤워실이 좁은 것이 아쉬웠다', '수영장', 0, 3]
['피트니스 근력 운동기구 다양했지만 사용법을 모르면 사용하기 어려웠다', '수영장', 0, 3]
['비록 추가 비용이 발생하지만 실내 수영장도 좋고 1층의 베이커리도 맛있습니다', '수영장', 1, 9]
['일단 평일 기준으로 가서 인지 가격도 저렴하게 예약할 수 있었고 수영을 좋아해서 실내 수영장을 애용했는데 투숙객 전용이어서 그런지 애들도 없고 여유롭게 수영했습니다', '수영장', 1, 14]
['유아는 라운지가 동반할 수 없어 조금 불편했지만 그 외 모든 것에 엄마가 굉장히 만족해 하셨습니다', '수영장', 1, 22]
['음식도 맛있고 전망도 좋고 룸도 훌륭하며 사우나도 좋다고 다음엔 이 모들과 다 같이 오자 고 하셔서 간 만에 효도 한 딸이 되었습니다', '수영장', 1, 22]
['호텔 피트니스 클럽과 실내 수영장도 이번에 처음 이용해봤어요', '수영장', 1, 26]
['라운지를 사용하면 따로 준비할 것이 크게 줄어 좋습니다', '수영장', 0, 35]
['다만 평일 내 아이들이 실내 수영장 이용이 불가한 점 미리 고지가 되었으면 좋겠습니다', '수영장', 1, 36]
['전망이 좋습니다', '수영장', 1, 37]
['라운지 이용을 할 수 있어서 좋은 점도 있지만 사람이 너무 많아 번 잡스러운 경우가 많아서 아쉽기도 합니다', '수영장', 0, 47]
['음식이나 룸 상태 사우나 모두 좋음', '수영장', 1, 56]
['겨울에 가서 저렴한 가격으로 이그제큐티브 라운지 이용했어요', '수영장', 1, 58]
['룸도 업그레이드 해 주시고 남산뷰 최고였습니다', '수영장', 1, 58]
['또 애프터눈티 저녁 조식 브런치 수영장 너무 알 찼어요', '수영장'

['이그제큐티브 라운지 이용 시 직원들의 서비스가 불만족했음', '수영장', 0, 714]
['더 라이브러리 애프터눈티는 비싸지만 맛은 없었음', '수영장', 0, 715]
['라운지에 만족함', '수영장', 1, 723]
['고층의 남산뷰 객실을 배정 받아서 밤낮으로 좋은 경치를 볼 수 있어서 힐링된 숙박이었습니다', '수영장', 1, 733]
['어반 아일랜드는 아이들이 많아서 실 내 수영장과 자쿠지 사우나를 이용하는 것을 추천', '수영장', 1, 740]
['공사 중이라서 숙소에서 내려 다 보는 야경이 조금 아쉬웠습니다', '수영장', 0, 742]
['다 만 아쉬운 점은 수영장이 공사 중이라서 야외를 이용하지 못한다는 점 그 부분 빼고 너무 만족스러웠습니다', '수영장', 0, 754]
['역시는 역시 다 수영을 좋아하는데 수영장 물이 염소 소독물이라 피부에 강하게 자극이 와서 붉게 달아올랐습니다', '수영장', 0, 765]
['수영장 물을 해수풀로 운영해주면 훨씬 좋을 것 같아요', '수영장', 0, 765]
['수영장도 재밌게 이용했고 조식도 맛있게 먹었어요', '수영장', 1, 767]
['크게 아쉬운 점은 없었지만 산책로 안내 야간에 호텔 밖으로 가는 길을 잘 찾지 못해 아쉬웠습니다', '수영장', 0, 770]
['서비스 및 조식 등 부대시설 피트니스 스파 만족스러웠습니다', '수영장', 1, 771]
['룸 컨디션도 좋았고 시티 뷰라 남산타워는 안 보였지만 시티뷰도 충분히 좋았어요', '수영장', 1, 773]
['수영장이 너무 이른 시간에 닫는다', '수영장', 0, 775]
['실내 수영장 내에 있는 자쿠지도 너무 좋았습니다', '수영장', 1, 776]
['룸 서비스나 야외 수영장 등 다른 시설 가격이 너무 비싸서 조금 아쉬웠습니다', '수영장', 0, 788]
['시설도 좋고 남산타워 보이는 것도 좋았어요', '수영장', 1, 789]
['아이들과 놀만한 데가 많지 않네요', '수영장', 0, 797]
['수영장 빼고는', '수영장

['로맨틱하게 보내기 좋음', '수영장', 1, 1102]
['장점 1 클럽 라운지 지금껏 서울에서 5 성급 호텔 10여군데에 투숙하면서 라운지 이용을 해보았는데 신라호텔 클럽 라운지 음식이 단연 최고로 훌륭했어요', '수영장', 1, 1107]
['3 어반 아일랜드 이용했던 날 날씨가 조금 쌀쌀했는데 메인 풀장 주변의 썬 베드에 열선이 설치되어 있어 불편하지 않게 이용할 수 있었습니다', '수영장', 1, 1107]
['단점 어반 아일랜드에 아이들을 데리고 노는 가족 이용객이 많았는데 키즈풀이 따로 있는 것을 보니 성인 이용객을 위해서 메인 풀과 키즈풀을 따로 운영하면 더 좋지 않을까라는 생각이 들었습니다', '수영장', 0, 1107]
['아이들이 많다', '수영장', 0, 1107]
['보니 여유 있게 놀기에 좀 힘든 점이 있더라구요', '수영장', 0, 1107]
['이그제큐티브 라운지를 이용하였는데 조용하고 번 잡스럽지 않았어요', '수영장', 1, 1111]
['밤 시간 실외 수영장 비록 사람은 많았지만 덥지도 않고 로맨틱하고 정말 좋았습니다 라운지 방문은 처음이었는데 음식은 평이 한 수준이었네요', '수영장', 1, 1116]
['실내 수영장도 남산 바라보며 쉬기에 아주 좋았습니다', '수영장', 1, 1117]
['남산에 4계절 풍경을 느끼실수 있습니다', '수영장', 1, 1121]
['룸과 라운지를 동시에 이용 할 수 있는 이그제큐티브 패키지로 다녀 왔습니다', '수영장', 1, 1126]
['중국 여행객들이 많아서 다소 소란스러웠던 점 그리고 주말 아이들과 함께 조식과 수영장을 즐기러 온 가족 단위 여행객으로 혼잡했던 점을 제외하고는 모든 것이 좋았던 것 같다', '수영장', 1, 1128]
['이그제 규티브룸으로 예약하고 가서 라운지를 이용했습니다', '수영장', 1, 1131]
['잠깐 들렸지만 수영장도 꽤 널찍하고 깨긋햇던 걸로 기억됩니다', '수영장', 1, 1133]
['입구의 기와 지붕이 정말 멋스러웠고 룸 컨디션도 정말 좋았어요

['호텔 부지 내에 있는 실행 추적은 3 왕복 이 아주 흥미진진한 지형 실행 중인 것 같은 흔적 또한 옥상 야외 헬스장 연결 추적을 실행 부페식 아침 식사와 연어 사시미 이 인상적이었어요', '수영장', 1, 1362]
['방을 예약했는데 라운지 수준 좋은 곳을 느끼는 데에 이 라운지에서 신라 이 인상적이었어요', '수영장', 1, 1363]
['방은 매우 좋고 세련되게 꾸며진 매우 편안한 침대 객실은 아주 넓고 훌륭한 시설 좋은 거대한 피트니스 센터 수영장은 환상적인 다만 사람이 너무 많 다', '수영장', 1, 1363]
['조금은 작았지만 아늑한 느낌 수영장이 놀랍다', '수영장', 1, 1365]
['서울 신라 호텔이 서울에 놀라운 아주 좋은 수영장이 있었습니다', '수영장', 1, 1368]
['호텔은 아주 넓고 큰 야외 산책하기를 즐겼다', '수영장', 1, 1370]
['또한 뛰어난 스파와 수영장 저는 이 리조트를 추천한 비즈니스 가족이 많았고 이곳 아이들은 자신을 즐기고', '수영장', 1, 1370]
['특히 수영장 내 방에서 볼 수 있는', '수영장', 1, 1371]
['3주 전에 여 자친구와 함께 갔는데 패키지 와이너리 입구에 있는 도시 섬 꼭대기 층에 있는 실 외 수영장이 그는 정말 놀라웠습니다', '수영장', 0, 1373]
['빠른 체크인 후 도시 섬상의 수영장에 갔다', '수영장', 1, 1373]
['멋진 전망은 나는 정말 사랑 한 도시 섬 상의 대신에 수영장과 치킨 맥주 방 이그제큐티브 스위트룸에 묵는 것 나 했는데 좋은 한밤중 이 또한 훌륭한 와이너리 라이브 밴드가 연주하는 재즈와 다양한 종류의 와인과 치즈를 제공하고 있고 꼭 대기 층에서 보이는 전망도 훌륭했습니다', '수영장', 1, 1373]
['라운지의 음식은 좋고 편안하고 아늑한 환경 라 도 산에 있는 택시를 타고 저녁을 인다의 그래도 다시 오고 싶다', '수영장', 1, 1374]
['녹음이 무성한 정원 수영장 피트니스 센터 스파 레스토랑 등 에도 멋진 서울 타워의 

[['도보로도 충분히 갈 수 있는 편리한 거리에 호텔 바로 앞 장충체육관 근처로 요거프레소와 편의점도 있어 편리했습니다',
  '주변',
  1,
  6],
 ['2 식당 한 중 일 식당으로 유명하죠', '주변', 0, 6],
 ['그냥 가보세요', '주변', 0, 68],
 ['영빈관 뷰도 좋아요', '주변', 1, 90],
 ['연결도 없고 그냥 짐 들고 올라가야 하니까요', '주변', 0, 97],
 ['하지만 주변에 이용할 만한 것들이 부족해서 다소 편의성은 떨어집니다', '주변', 0, 124],
 ['레스토랑 부대시설 다 좋음', '주변', 1, 153],
 ['워낙 유명하니', '주변', 0, 163],
 ['매끼니 걱정할 필요 없고', '주변', 1, 249],
 ['편의 등 등', '주변', 1, 380],
 ['다만 주차장과 연결 되어 있지 않아 아쉬웠습니다', '주변', 1, 403],
 ['영빈관 뷰 아름답고 좋습니다', '주변', 1, 430],
 ['주변에 즐길거리가 없어서 호텔 내 시설을 최대한 이용하는 것이 좋을 것 같습니다', '주변', 0, 498],
 ['산책할 수 있는 공간 편안히 즐겼던', '주변', 1, 661],
 ['이게 호텔이지 느끼게 해줌 편의점이 멈ㅠ 서민 마인드', '주변', 0, 674],
 ['남산이 한 눈에 들어오는 뷰라서 좋았고 호텔 주위를 볼 수 있어 좋았습니다', '주변', 1, 705],
 ['최근에 다른 호텔에 가면 지하에 씨유 편의점이 있더라고요 룸에 있는 미니바 이용이 맞긴 한데', '주변', 0, 812],
 ['개인적 욕심으로 여기도 지하 쇼핑 아케이드에 편 의점 매장 하나 있으면 좋겠다 싶었습니다', '주변', 0, 812],
 ['그리고 1층 식당 너무 비싼데 맛이 없어요 ㅠㅠ', '주변', 0, 896],
 ['저녁에는 일몰도 이 쁘게 볼 수 있었습 니다 가까운 거리에 이태원 디 뮤지엄이 있어 문화생활을 하기에도 좋은 위치라고 생각이 들었습니다',
  '주변',
  1,
  965],

In [11]:
df1 = pd.DataFrame(result)
df1.to_csv('data/test/dummy.txt', index = False)

In [13]:
result1 = [[['a',1], ['b', 2], ['c', 3]],
          [['d',1], ['e', 2], ['f', 3]],
          [['g',1], ['q', 2], ['w', 3]]
         ]

In [14]:
result2 = [['a','b','c'],
          ['d','e','f']
         ]

In [15]:
result2[0]

['a', 'b', 'c']

In [104]:
category['1']

0       1
1      10
2      10
3       7
4       0
5      10
6      10
7       1
8       5
9       0
10      4
11      4
12      1
13     13
14     13
15     10
16     11
17      4
18      1
19      4
20     14
21      5
22     14
23     14
24     14
25      1
26     11
27     12
28      4
29      1
30     14
31     13
32      4
33      1
34      4
35      1
36      8
37      1
38      7
39     14
40     14
41     14
42     14
43      1
44      5
45      0
46      4
47      1
48      1
49      4
50      4
51      4
52      1
53      1
54      7
55     13
56      4
57     13
58      1
59      4
60      4
61      0
62      4
63     13
64     10
65      4
66     13
67     13
68     14
69      1
70      4
71      1
72     13
73     10
74     14
75      4
76     13
77      7
78     14
79      5
80     13
81      1
82      7
83     10
84     13
85      4
86      1
87     13
88     14
89     14
90     10
91     10
92     14
93      2
94      3
95      3
96      6
97     16
98      1
99     14


In [144]:
folder_name = 'data/test/'
categoryResultFile = folder_name + 'Word2Vec' + '_17_result.txt'
category = pd.read_csv(categoryResultFile, sep= ',')
tmp = 15
cnt = len(category['1'].unique())
a = category.groupby('1').get_group(tmp)
a

FileNotFoundError: [Errno 2] No such file or directory: 'data/test/Word2Vec_17_results.txt'

KeyError: 'Column not found: 0'

In [ ]:
columns_list = list(category)
test_dataset = []
for col_name in columns_list:
    tmp = category[col_name].dropna(axis=0)
    test_dataset.append(NHSDataset(tmp))

In [25]:
[i[0] for i in result1[0]]

['a', 'b', 'c']

In [34]:
pd.set_option('display.max_rows', 50000)
# 최대 열 수 설정
pd.set_option('display.max_columns', 50000)
# 표시할 가로의 길이
pd.set_option('display.width', 10000)

In [75]:
df1 = pd.read_csv('data/key_raw/small_test.csv', sep= ',')
df2 = pd.read_csv('data/key_pre/small_test.txt', sep= '\t')
for idx, item in enumerate(df1['ReviewText']):
    print('-----------')
    print(idx)
    print(item)
    

-----------
0
친구들하고 오랜만에 급 계획으로 예약하여 호캉스 다녀왔습니다. 호텔 주변에 음식점도 많고 부대시설도 잘되어있어서 편햇습니다~ 그리고 바로 역도 가까이 있어서 이동이 편하더라구요! 그런데 객실이 좀 많이 낙후되어 있더라구요..그 점을 빼곤 서비스 전체 모든면에서 괜찮았습니다!
-----------
1
신사역에 있어서 가로수길이나 압구정동은 걸어서도 구경하러 편하게 다녀올 수 있었고
택시를 타도 한남동이나 이태원, 강남역까지 10분안에 이동이 가능했습니다.
강남 고속터미널도 호텔 앞에 지하철을 타니 2정거장!
위치 정말 최고로 마음에 들었습니다.
여행다니면서 숙소가 구석진데 있으면 왔다갔다 시간낭비, 교통비 낭비가 너무 아까운데
가족들도 다 매우 편한하다고 만족했어요~ 이 부분 너무 좋네요!

프론트 데스크 직원들의 친절한 서비스도 여행 내내 참 기분좋아지게 만들어주었습니다.
뷔페가 유명한 호텔답게 조식도 알차고 맛있었네요~
아침에 가볍게 먹을 수 있는 죽이나 스프종류도 많았고,
메인 요리도 제법 많아서 아침 한끼 식사로는 조금 과하다 싶을만큼
푸짐했습니다. 아이들도 정말 맛있게 잘먹었어요^^

이 가격에 이런 호텔을 국낸에서 이용하다니, 이거 실화인가요? ^^
저는 정말 만족하게 잘 머물다 왔습니다~~!
-----------
2
근처 다른 호텔에비해 객실비가 싸고 번화가에서도 가까워서 예약했었는데, 룸컨디션은 한강뷰도 넘 좋았고 했지만, 지하주차장이 너무 노후해서 별로였어요. 발렛맡겼을때는 몰랐는데 직접갔을때는 이게 호텔주차장이 맞나 싶을정도로 낙후한...
외국인손님 모시고 가기엔 별로요~
-----------
3
뷔페음식이 가격 대비 훌륭합니다. 프로모션 할때 방문하면 더 만족도가 높습니다. 호텔 뷔페 답게 다양한 음식이 잘 준비되어 있습니다
-----------
4
무슨 호텔이 이럴까! 호텔이라고 부를 수 없을 정도. 피트니스 청소를 얼마나 하지 않았으면 1주일이 넘어도 컵이 그대로 있고. 여기저기 먼지가 수북. 락커에도 먼지가. 목

In [76]:
df2

text  rawSentenceIdx
0                    친구들하고 오랜만에 급 계획으로 예약하여 호캉스 다녀왔습니다               0
1                  호텔 주변에 음식점도 많고 부대시설도 잘 되어 있어서 편햇습니다               0
2                         그리고 바로 역도 가까이 있어서 이동이 편하더라구요               0
3                              그런데 객실이 좀 많이 낙후되어 있더라구요               0
4                         그 점을 빼곤 서비스 전체 모든 면에서 괜찮았습니다               0
5    신사역에 있어서 가로수길이나 압구정동은 걸어서도 구경하러 편하게 다녀올 수 있었고 ...               1
6    강남 고속터미널도 호텔 앞에 지하철을 타니 2 정거장 위치 정말 최고로 마음에 들었습니다               1
7    여행 다니면서 숙소가 구석진데 있으면 왔다갔다 시간 낭비 교통비 낭비가 너무 아까운...               1
8                                          이 부분 너무 좋네요               1
9      프론트 데스크 직원들의 친절한 서비스도 여행 내내 참 기분 좋아지게 만들어 주었습니다               1
10                          뷔페가 유명한 호텔답게 조식도 알차고 맛있었네요               1
11   아침에 가볍게 먹을 수 있는 죽이나 스프 종류도 많았고 메인 요리도 제법 많아서 아...               1
12                                  아이들도 정말 맛있게 잘 먹었어요               1
13                  이 가격에 이 런 호텔을 국낸에서 이용하다니 이 거 실화인가요               1
14                               저는 정말 만족하게 잘 머물다 왔습니다               1
15   근처 다른 호텔에 비해 객실비가 싸고 번화가에서도 가까워서 예약했었는데 룸 컨디션은...               2
16   발렛 맡겼을 때는 몰랐는데 직접 갔을 때는 이게 호텔 주차장이 맞나 싶을 정도로 낙...               2
17                                  뷔페 음식이 가격 대비 훌륭합니다               3
18                           프로모션 할 때 방문하면 더 만족도가 높습니다               3
19                        호텔 뷔페 답게 다양한 음식이 잘 준비되어 있습니다               3
20                                          무슨 호텔이 이럴까               4
21   호텔이라고 부를 수 없을 정도 피트니스 청소를 얼마나 하지 않았으면 1주일이 넘어도...               4
22                목욕탕에는 스마트폰 사용하는 자들이 득실거리고 ㅎ 직원이 누구인지               4
23                                  리버 사이드 모텔로 이름 바꿔 라               4
24                                   호텔이라는 이름을 더럽히지 말고               4
25        가족 모임이 있어 리버 사이드 뷔페를 다녀와 서 차에 심한 기스를 발견 했습니다               5
26   일단 자가 주차가 안 되고 발레 주차만 가능한데 주말에는 이용자가 많아 너무 복잡하...               5
27                주차 팀장과 통화한 결과 호텔은 잘못한 게 없다는 답을 받았습니다               5
28   뷔 폐도 사람이 너무 많아 식사 하는 시간보다 줄 서서 기다리는 시간이 더 길고 음...               5
29   참고로 수프는 다 식어서 나오고 고기는 급하게 나오다 보니 안에 피가 흥건히 고 여...               5
30                               만약 가야 되면 차는 집에 두고 가세요               5
31                                가격 대비 괜찮은 뷔페라고 생각합니다               6
32             음식 가짓수가 정말 많은데 아쉬운 건 초밥이나 스 시류가 적은 편입니다               6
33                         단체로 모임이나 연회 장소로 적합하다고 생각합니다               6
34                               연회장 앞에 방이 있는 게 말이 되나요               7
35      정말 어 이가 없어서 문도 다 열어놓고 결혼식에 동창회에 사람이 묵을 곳이 아닙니다               7
36              특히 저녁 시간은 내내 노래 부르고 마이크로 방송하고 정말 저질입니다               7
37                                  절대 묵지 마시길 너무 후회됩니다               7
38                                             외관은 멋있음               8
39                        객실 이용 고객 주차 무료 레스토랑 질 좋고 맛있음               8
40                   하지만 객실은 너무 낡아서 숙박은 다시 하고 싶진 않았습니다               8
41   의전을 위해서 선택했던 곳인데 호텔이라고 하기엔 객실이 모텔보다 못한 듯 하고 객실...               9
42                 오래된 호텔이기도 했지만 내부 수리가 좀 필요하다 생각이 드네요              10
43                 특히 화장실 쪽이 급해서 하루 묵었지만 추천 하고 싶지가 않네요              10
44   우선 지하철역이랑 가까운 편이 이라서 괜찮았는데 객실 청소가 제대로 안 되어 있어서...              11
45                                 직원 분들은 친절하고 좋았는데 ㅠㅠ              11
46                          리버 사이드 호텔 뷔페 더가든 키친 다녀왔습니다              12
47                               저는 예약 없이 일요일 디너 방문했는데              12
48                              가족 단위 손님이 많아 대기가 길었습니다              12
49   저녁은 6시부터 시작인데 뷔폐에서 가까운 좌석을 원하시면 꼭 사 전에 예약하고 가 ...              12
50          리버 사이드 호텔 뷔페는 깔끔하고 서비스도 좋고 무엇보다 재료가 정말 좋아요              12
51                                        맛있게 잘 먹고 갑니다              12
52                               부페식당이 상대적으로 저렴하고 좋습니다              13
53                                     연말 모임으로 인기가 많아요              13
54                                     거의 매년 이용하고 있습니다              13
55   친구와 함께 1박했는데 시설이 세련되거나 새로운 느낌은 아니지만 무난하고 편안한 느...              14
56 

In [54]:
df = pd.DataFrame(columns = ['1','2'])
df = df.append({'1':0, '2':0}, ignore_index=True)

In [77]:
df3 = pd.read_csv('data/key_raw/train.csv', sep= ',')

In [85]:
t = df3['ReviewText'].iloc[15602]

In [86]:
str(t)

'nan'

In [97]:
d = [('소리', 3944),('방음', 2191),('소음', 1860)]

In [98]:
d[:2]

[('소리', 3944), ('방음', 2191)]

In [99]:
[item[0] for item in d[:2]]

['소리', '방음']

In [148]:
dff = pd.read_csv('data/test/FastText_results.txt')
dff

0   1                                                  2
0        0   1       결혼기념일을 맞아 방문했는데 역시나 좋은 시설과 서비스로 즐거운 시간 보냈습니다
1        1  11               클럽룸으로 이그제큐티브 라운지를 이용하였는데 총 네 번 이용했어요
2        1  12                     에프터눈 티랑 디너랑 조식이랑 해피아워 였던 거 같아요
3        1   3                  호텔리어들의 서비스랑 하우스키퍼들도 훌륭하였고 다 괜찮았어요
4        1  11                                호캉스를 한다면 클럽 룸을 추천해요
5        1   0            굳이 호텔 밖으로 나갈 필요도 없고 라운지만 이용해도 배가 엄청 불러요
6        1   1                그치만 다시 예약한다면 아고다만의 메리트는 딱히 없는 거 같아요
7        1   0  다시 신라를 예약하면 공식 홈페이지에서 할 거 같아 요 가격 측면에서도 딱히 저렴한...
8        1   5                           그냥 공식 홈페이지에서 예약하는 걸 추천해요
9        2   7              숙소의 위치 업무 편의성 모든 게 편안한 출장 계속 이용하려 합니다
10       3   3             성수기라 체크인 시간은 좀 걸렸지만 직원들의 태도와 친절도가 우수했다
11       3  11                                 실내 수영장도 개방형이라서 좋았다
12       3  11                                수영장 샤워실이 좁은 것이 아쉬웠다
13       3   2                               객실 인테리어 및 편의시설은 훌륭했다
14       3  15                                   화장실 및 욕실은 최상급이였다
15       3  11              피트니스 근력 운동기구 다양했지만 사용법을 모르면 사용하기 어려웠다
16       3   3                   체크아웃까지 정말 친절하게 모든 필요를 채워주셔서 감사했다
17       4   5  체크인이 원래 3시 반인데 전날 밤을 새서 너무 피곤해 하며 두 시간 더 일찍 갔는...
18       4  10                                      란 생각이 마구 들더군요
19       4   2  신라는 반얀에 비해 층 고도 높고 룸도 쾌적하고 시설도 더 깔끔하고 조식이 훨씬 맛...
20       4   1             이전에 투숙했을 때나 이번에 나 직원 분들이 지인 짜 친절하 셨습니다
21       4   3                        매번 이 친절 때문에 또 오고 싶단 생각이 듭니다
22       4  10             방문했던 5성급 호텔들 중 가격 대비 제일 만족도가 높은 것 같습니다
23       4   5                             체크아웃이 12시 인 것도 마음에 듭니다
24       4   0                           비즈니스 고객들한테 특히 더 좋을 듯 합니다
25       4  15  단점은 화장실 휴지걸이가 힘이 없고 헐거워서 자꾸 빠지는 것 정도 여튼 출장 투숙객...
26       5   0                     하도 좋다는 말을 많이 들어서 오히려 기대는 안했습니다
27       5   3  들어가자마자 저와 친구의 짐을 확인하고 들어주시는데 거기서 1차 충격 감동 체크인 ...
28       5   1              저는 이번 1박 2일 주말 숙박 동안 직원 분들께 너무 감사했습니다
29       5   3           짧은 멘트에도 느껴지는 친절은 신라에서만 느낄 수 있을 거라 생각됩니 다
30       5   0                                  프라이드가 굉장할 거라 생각해요
31       5   5  더 파크뷰 조식 먹으러 갈 때 객실 실내화를 신고 갔는데 ㅎㅎㅎ 매니저분인지 민망하...
32       5   3                               정말 멋지고 멋진 직원 분들이였습니다
33       6   7                       1 첫 번째 위치 오는 길 역이랑 상당히 가깝습니다
34       6   7  도보로도 충분히 갈 수 있는 편리한 거리에 호텔 바로 앞 장충체육관 근처로 요거프레...
35       6   4        차량을 소지하셔서 운전하시고 오신다면 발렛 서비스도 상당히 괜찮다고 생각합니다
36       6   7                               2 식당 한 중 일 식당으로 유명하죠
37       6   0  이용하진 않았습니다만 전체적인 메뉴도 균형 잡혀 있고 손님 접대 시 아주 괜찮다고 ...
38       6  12  뿐만 아니라 더 파크뷰의 요리는 훌륭했습니다 고기가 가끔 오버쿡 되어 있던 것들이 ...
39       6  12      아이들이 먹을 만한 메뉴는 빵 리조 또 등이 있지만 다채롭지는 않다고 생각했습니다
40       6  12                                       커피가 아주 훌륭했어요
41       6   2                      3 청결 서비스 숙소 내 청결도는 상당히 만족했습니다
42       6   5  각 잡혀 있는 미니바에서 부터 빨래 서비스도 좋았고 얼음과 의자를 부탁드렸었는데 아...
43       6   5  체크아웃까지도 요구했던 빨래가 도착하지 않아 걱정했는데 여유롭게 나와도 괜찮다며 아...
44       7   4                           주차부터 퇴실 때까지 너무 친절하고 좋았어요
45       7   6                      가드 설치도 따로 해주셔서 아기도 안전하게 잘 잤구요
46       8   1                                       아기랑 함께 이용했어요
47       8   4  따로 발렛을 하지 않았더니 주차타워로 안내해줬는데 주차타워에 엘리베이터가 없어서 정...
48       8  10                       그래서 숙소 편의와 부대시설에서 별 두 개 깎았어요
49       8   5  직원들은 매우 친절하셨고 아기 침대 신청했더니 방에 미리 설치해 주셔서 너무 잘 이...
50       8  12  조식을 따로 신청하는 것이 저렴할 것 같아 조식도 체크인하며 신청해서 먹었는데 맛있었어요
51       8   5                    아기를 위해서 흰 죽도 따로 끓여주셔서 배려에 감동했네요
52       9  11         비록 추가 비용이 발생하지만 실내 수영장도 좋고 1층의 베이커리도 맛있습니다
53       9  12                                        조식도 훌륭해요 ㅎㅎ
54      10   3  이그제큐티브 라운지 여자 직원분께서 친절하게 응대해주시고 꽃다발보시더니 기념일이시냐...
55      10   1                주말인데 룸 업그레이드도 받고 미리 예약해서 싸게 다녀 왔습니다
56      10  12                          음식은 먹다 보면 질리기는 하지만 괜찮았습니다
57      10   1                         다음 기념일에도 괜찮은 가격이면 다시 올려 구요
58      11   2                                            분위기 좋아요
59      13   2                                   

In [157]:
dff1 = pd.read_csv('data/test/dummy.txt')
dff1

text category  sentiment  rawsentenceIdx
0     도보로도 충분히 갈 수 있는 편리한 거리에 호텔 바로 앞 장충체육관 근처로 요거프레...       주변          1               6
1                                  2 식당 한 중 일 식당으로 유명하죠       주변          0               6
2                                               그냥 가보세요       주변          0              68
3                                            영빈관 뷰도 좋아요       주변          1              90
4                              연결도 없고 그냥 짐 들고 올라가야 하니까요       주변          0              97
5                 하지만 주변에 이용할 만한 것들이 부족해서 다소 편의성은 떨어집니다       주변          0             124
6                                        레스토랑 부대시설 다 좋음       주변          1             153
7                                               워낙 유명하니       주변          0             163
8                                         매끼니 걱정할 필요 없고       주변          1             249
9                                                편의 등 등       주변          1             380
10                           다만 주차장과 연결 되어 있지 않아 아쉬웠습니다       주변          1             403
11                                      영빈관 뷰 아름답고 좋습니다       주변          1             430
12         주변에 즐길거리가 없어서 호텔 내 시설을 최대한 이용하는 것이 좋을 것 같습니다       주변          0             498
13                                  산책할 수 있는 공간 편안히 즐겼던       주변          1             661
14                        이게 호텔이지 느끼게 해줌 편의점이 멈ㅠ 서민 마인드       주변          0             674
15            남산이 한 눈에 들어오는 뷰라서 좋았고 호텔 주위를 볼 수 있어 좋았습니다       주변          1             705
16    최근에 다른 호텔에 가면 지하에 씨유 편의점이 있더라고요 룸에 있는 미니바 이용이 ...       주변          0             812
17    개인적 욕심으로 여기도 지하 쇼핑 아케이드에 편 의점 매장 하나 있으면 좋겠다 싶었습니다       주변          0             812
18                           그리고 1층 식당 너무 비싼데 맛이 없어요 ㅠㅠ       주변          0             896
19    저녁에는 일몰도 이 쁘게 볼 수 있었습 니다 가까운 거리에 이태원 디 뮤지엄이 있어...       주변          1             965
20                                     4시간 저온 가열했다고 합니다       주변          0             970
21                                     괜히 유명한 게 아닌 것 같다       주변          1             975
22                                       아직 포시진은 못 가봤네요       주변          1             978
23                  주변을 잘 몰라 서성 대자 먼저 다가와서 어 프러치 해주었습니다       주변          1             984
24                                                포장 가능       주변          1            1020
25                             서울둘레길 따라서 산책할 수 있어서 좋습니다       주변          1            1024
26                       식사 중간 중간 편의를 봐주어 더욱 좋았던 것 같습니다       주변          1            1043
27                                 이후 면세점 들려 몇 가지 좀 사는데       주변          0            1056
28                                       공정거래위원회는 무엇하는지       주변          0            1057
29                                    특히 야외자쿠지가 너무 좋았고요       주변          1            1117
30    도 하지만 개인적으로 높은 곳에 위치해 있어 편의점이나 주변 관광지로 가는 길이 먼...       주변          0            1136
31      업무차 방문한 서울 신라호텔입니다 면세점이 가까이에 있어서 쇼핑하기에도 아주 좋습니다       주변          1            1145
32                                       신라호텔은 전무후무하니깐요       주변          1            1153
33            또한 면세점과 인근에 맛집이 많아 큰 이동 없이 여유를 즐길 수 있었습니다       주변          1            1167
34                                    면세점 바로 옆에 있어 편하구요       주변          1            1190
35                                호텔 주변 환경이 산책하기에도 좋습니다       주변          1            1194
36                                근처에 쇼핑몰도 많아 구경거리도 많아요       주변          1            1225
37         근처 먹거리도 많고 상점들의 접근이 좋으며 호텔은 안쪽에 위치하고 있어 조용하다       주변          1            1230
38    인근에 저녁을 하러 나간다든지 짐을 들고 방문할 때 택시가 필수인 만큼 접근성은 다...       주변          1            1235
39                                함께 있는 면세점 또한 만족할 것입니다       주변          1            1250
40                            그러나 어쩔 수 없지만 뷰는 정말 심심했습니다       주변          0            1258
41                                   물론 면세점에는 3번이나 갔습니다       주변          1            1277
42    일단 병설된 면세점 이외에 호텔 지하에서도 쇼핑을 즐길 수 있습니다 면세점에도 있는...       주변          1            1278
43 

In [159]:
category = dff1['category'].unique()

In [167]:
result = dff1.groupby('category').get_group('소리')
result

text category  sentiment  rawsentenceIdx
2865                                        단점은 일단 없습니다       소리          0             206
2866  방음도 잘 되어 노래 틀고 놀아도 민원이 없었다는 점도 만족스럽고 룸 컨디션도 좋았습니다       소리          1             423
2867                                단점은 차 없으면 올라가기 힘듬 끝       소리          0             460
2868                공사 중이고 방 간에 방음이 잘 되지 않은 편이라 시끄러웠습니다       소리          0             484
2869                방음상 태 나 쁨 옆방 아이들 떠드는 소리 신경 쓰일 정도였어요       소리          0             495
2870         전반적으로 다 좋았지만 방에서 복도나 다른 방 소음이 잘 들려서 아쉬웠습니다       소리          0             719
2871                                공사가 끝나면 문제는 없을 듯합니다       소리          0             731
2872                                    근데 입고 자기엔 까실거려요       소리          0             747
2873                                   층 간 방음이 약해서 아쉬웠다       소리          0             825
2874                                 호캉스족들이 모려와 난리도 아니야       소리          0             893
2875                                          공사 중 어수선함       소리          0             905
2876  모처럼 푹 자고 싶어서 예약한 거였고 남산 전망 객실이었는데 아무래도 오토바이 소리...       소리          0             921
2877                    출입구 센서 등이 고장 나서 새벽에 직원을 다 불렀습니다       소리          0             946
2878    단 밤에 잠을 잘 때 히터기에서 이상한 소리가 규칙적으로 들려서 잠을 잘 못 잤습니다       소리          0            1079
2879               도저히 잠을 못 자서 새벽 3시에 다른 방으로 옮겨서 자게 됬어요       소리          0            1079
2880             단점 건물이 오래되서 그런지 복도 사이가 좁아서 방음이 잘 안 됩니다       소리          0            1156
2881                                        복도 소움이 들리네요       소리          0            1156
2882           매우 바쁜 호텔이 우리가 묵는 동안 방에 있는 복도 소음이 되지 않습니다       소리          1            1295
2883  단점은 채 옆에 면세점 을 수 있지만 좋은 말 그대로 수백 개 수백 개의 중국 본토...       소리          0            1507

In [168]:
results = []
cnt = dff1.shape[0]
for item in category:
    result = dff1.groupby('category').get_group(item)
    pos = result['sentiment'].sum()
    neg = result['sentiment'].shape[0] - pos
    tmp = [item, result['sentiment'].shape[0]/cnt * 100, pos, neg]
    results.append(tmp)
results

[['주변', 1.2896825396825395, 46, 19],
 ['기타', 23.035714285714285, 760, 401],
 ['가격', 6.805555555555555, 255, 88],
 ['침대', 3.511904761904762, 110, 67],
 ['냄새', 1.646825396825397, 19, 64],
 ['직원', 10.357142857142858, 435, 87],
 ['체크', 10.198412698412698, 158, 356],
 ['소리', 0.376984126984127, 2, 17],
 ['에어컨', 0.7738095238095238, 14, 25],
 ['조식', 11.765873015873016, 437, 156],
 ['화장실', 0.8531746031746031, 24, 19],
 ['위치', 2.956349206349206, 105, 44],
 ['어메니티', 1.130952380952381, 31, 26],
 ['이용', 9.563492063492063, 388, 94],
 ['깨끗', 5.952380952380952, 278, 22],
 ['수영장', 9.781746031746032, 354, 139]]

In [171]:
sum_ = 0
for r in results:
    sum_+= r[1]
sum_

100.0

In [162]:
result = dff1.groupby('category').get_group('주변')
result['sentiment'].sum()

46

In [164]:
result['sentiment'].shape[0]

65